# Load Data

In [36]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

from sklearn.model_selection import train_test_split

from sklearn.preprocessing import StandardScaler
from sklearn.linear_model import LinearRegression
from sklearn.feature_selection import SelectFromModel

import pickle

import gc
import os
working_directory = 'D:\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'  ## 서로 다른 환경에서는 이곳을 수정해야 함.
# working_directory = 'C:\\Users\\user\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'

os.chdir(working_directory)
gc.collect()

# load dataset
coin = 'BTC'
target_var = 'dv5_realized_volatility_mean0'
target_var_3 = target_var[:3]

data = pd.read_csv("./output/{}_sum_plus_nn_features_for_{}.csv".format(coin, target_var_3))


# In practice, feature selection should be done after data pre-processing,
# so ideally, all the categorical variables are encoded into numbers,
# and then you can assess how deterministic they are of the target

# here for simplicity I will use only numerical variables
# select numerical columns:

numerics = ['int16', 'int32', 'int64', 'float16', 'float32', 'float64']
numerical_vars = list(data.select_dtypes(include=numerics).columns)
data = data[numerical_vars]

In [37]:
print(data.shape) # Check the shape of NN file.

pd.set_option('display.max_columns', None)
data.head(3) 

# five features are dep.
# so, # of features after adding NN features is 18,237.

(75169, 7144)


realized_volatility_mean0  num_trades  lowest_return  highest_return  \
0                   0.000105    2.575188      -0.000089        0.001815   
1                   0.000107    2.557507      -0.000089        0.001815   
2                   0.000106    2.562293       0.000000        0.001815   

   high_low_gap  trade_vol  BB_width_w20  BB_width_w40  BB_width_w10  \
0      0.001904   1.138501  48144.956559  47257.071103  55194.202594   
1      0.001904   1.100893  50564.809898  50311.440306  54273.382058   
2      0.001815   1.124306  53873.536126  53013.302636  51861.353627   

   dv5_realized_volatility_mean0  realized_volatility_mean0_150  \
0                       0.000154                       0.000046   
1                       0.000156                       0.000077   
2                       0.000159                       0.000140   

   num_trades_150  lowest_return_150  highest_return_150  high_low_gap_150  \
0              85          -0.000089            0.000089          0.000177   
1              68          -0.000089            0.000354          0.000443   
2              69           0.000000            0.000354          0.000354   

   trade_vol_150  realized_volatility_mean0_300  num_trades_300  \
0       3.814411                       0.000100             147   
1       1.921894                       0.000106             126   
2       2.159312                       0.000109             125   

   lowest_return_300  highest_return_300  high_low_gap_300  trade_vol_300  \
0          -0.000089            0.000354          0.000443       5.543539   
1          -0.000089            0.000399          0.000487       3.760741   
2           0.000000            0.000753          0.000753       4.498119   

   realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
0                       0.000092             209          -0.000089   
1                       0.000116             259          -0.000089   
2                       0.000119             286           0.000000   

   highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
0            0.001284          0.001373       9.178568   -2.503398   
1            0.001815          0.001904       9.098996   -2.887379   
2            0.001815          0.001815       9.661851   -2.787476   

   liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  \
0   -2.492577   -2.457350    -2.437520    -2.411095  0.000475  0.000668   
1   -2.786359   -2.687438    -2.633461    -2.614329  0.000472  0.000647   
2   -2.785780   -2.635687    -2.586336    -2.562354  0.000489  0.000659   

   ep_liq_5  ep_liq_10  ep_liq_15  bidask_spread_0  bidask_spread_1  \
0  0.001029   0.001296   0.001752         2.030769        10.261539   
1  0.000948   0.001205   0.001527         2.098361        13.000000   
2  0.000952   0.001197   0.001454         1.487500         9.412500   

   liq_last_1_150  liq_last_2_150  liq_last_5_150  liq_last_10_150  \
0        0.001555        0.001703        0.002171         0.002716   
1        0.000299        0.000458        0.000700         0.001334   
2        0.000284        0.001064        0.001406         0.001930   

   liq_last_15_150  ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  \
0         0.003101      0.001283      0.001609      0.002627       0.002997   
1         0.001723      0.000869      0.001128      0.001713       0.002192   
2         0.002127      0.000514      0.000769      0.001105       0.001656   

   ep_liq_15_150  bidask_spread_0_150  bidask_spread_1_150  liq_last_1_300  \
0       0.004168             2.000000             9.000000        0.000238   
1       0.002849             5.636363             9.000000        0.001734   
2       0.002048             6.533333             8.533334        0.000070   

   liq_last_2_300  liq_last_5_300  liq_last_10_300  liq_last_15_300  \
0        0.000819        0.002223         0.003171         0.003458   
1        0.002134        0.002249         0.0027

# Remove Row Data to Selection

In [38]:
print("Before remove target_var's threshold : " , data.shape)

# 'dv1_realized_volatility' 열의 25%와 75% 백분위수 계산 => dv5
percentile_25 = data[target_var].quantile(0.25)
percentile_75 = data[target_var].quantile(0.75)

# 0~25%와 75~100% 범위 밖의 행 제거
data_q1q4 = data[(data[target_var] <= percentile_25) | (data[target_var] >= percentile_75)]

print("After remove target var's threshold : " , data_q1q4.shape)

Before remove target_var's threshold :  (75169, 7144)
After remove target var's threshold :  (37586, 7144)


In [39]:
y = data_q1q4[target_var]
# drop_list = [] # 'dv1_realized_volatility','dv2_lowest_return','dv3_highest_return','dv4_realized_volatility_30s','dv5_realized_volatility_mean0'
# drop_list.append(target_var)
X = data_q1q4 # .drop(drop_list, axis=1)
# X = data_q1q4.drop(['realized_volatility', 'realized_volatility_150', 'realized_volatility_300', 'realized_volatility_450'], axis=1)
# print(X.shape)

# Feature Selection (0)
## Remove Corrlative Features

In [40]:
def correlation(dataset, threshold, target_var):
    col_corr = set()  # Set of all the names of correlated columns
    corr_matrix = dataset.corr()
    
    print("correlation calculation, done") 

    for i in range(len(corr_matrix.columns)):
        if i % 10 == 0:
            print("progress:", "{:.2f}".format((i/len(corr_matrix.columns)*100)), "%")        
        for j in range(i) :
            if (abs(corr_matrix.iloc[i, j]) > threshold) & (abs(corr_matrix.iloc[i, j]) < 1): # we are interested in absolute coeff value
                
                # Drop one of them with lower correlation with our target variable.
                if corr_matrix[target_var][i] >= corr_matrix[target_var][j]:
                    colname = corr_matrix.columns[j]  # getting the name of column
                elif corr_matrix[target_var][i] < corr_matrix[target_var][j]:
                    colname = corr_matrix.columns[i]  # getting the name of column        
                col_corr.add(colname)
                
    return col_corr

# note that we reduce the correlation threshold
# to remove more features
corr_cutpoint = 90
corr_features = correlation(X.sample(n=2000, random_state=42), corr_cutpoint/100, target_var)
print('correlated features: ', len(set(corr_features)) )

correlation calculation, done
progress: 0.00 %
progress: 0.14 %
progress: 0.28 %
progress: 0.42 %
progress: 0.56 %
progress: 0.70 %
progress: 0.84 %
progress: 0.98 %
progress: 1.12 %
progress: 1.26 %
progress: 1.40 %
progress: 1.54 %
progress: 1.68 %
progress: 1.82 %
progress: 1.96 %
progress: 2.10 %
progress: 2.24 %
progress: 2.38 %
progress: 2.52 %
progress: 2.66 %
progress: 2.80 %
progress: 2.94 %
progress: 3.08 %
progress: 3.22 %
progress: 3.36 %
progress: 3.50 %
progress: 3.64 %
progress: 3.78 %
progress: 3.92 %
progress: 4.06 %
progress: 4.20 %
progress: 4.34 %
progress: 4.48 %
progress: 4.62 %
progress: 4.76 %
progress: 4.90 %
progress: 5.04 %
progress: 5.18 %
progress: 5.32 %
progress: 5.46 %
progress: 5.60 %
progress: 5.74 %
progress: 5.88 %
progress: 6.02 %
progress: 6.16 %
progress: 6.30 %
progress: 6.44 %
progress: 6.58 %
progress: 6.72 %
progress: 6.86 %
progress: 7.00 %
progress: 7.14 %
progress: 7.28 %
progress: 7.42 %
progress: 7.56 %
progress: 7.70 %
progress: 7.84 %
p

In [41]:
# Set을 List로 변환
corr_features = list(corr_features)

# List를 Pickle로 저장
with open('corr_del_list_{}_{}_{}.pkl'.format(coin, target_var_3, corr_cutpoint), 'wb') as f:
    pickle.dump(corr_features, f)



In [42]:
# 저장된 Pickle 파일을 로드하는 방법
with open('corr_del_list_{}_{}_{}.pkl'.format(coin, target_var_3, corr_cutpoint), 'rb') as f:
    corr_features = pickle.load(f)

print(len(corr_features))

2148


In [43]:
# correlation 이 다른 변수와 높은 변수는 삭제한다.
X.drop(labels=corr_features, axis=1, inplace=True)

# target var 도 이제 X에서 제거한다.
X.drop(target_var, axis=1, inplace=True)

c:\Users\hhkim\AppData\Local\Programs\Python\Python37\lib\site-packages\pandas\core\frame.py:4913: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [44]:
X.shape

(37586, 4995)

In [45]:
X.head(3)

realized_volatility_mean0  num_trades  highest_return  high_low_gap  \
27                   0.000197    2.805501        0.000841      0.001416   
34                   0.000177    2.773055        0.000088      0.001771   
35                   0.000187    2.751279        0.000044      0.001815   

    BB_width_w20  BB_width_w40  realized_volatility_mean0_150  \
27  40395.935178  69310.967793                       0.000225   
34  45608.863404  53481.460962                       0.000221   
35  48417.482706  53664.771427                       0.000288   

    lowest_return_150  highest_return_150  high_low_gap_150  \
27          -0.000576            0.000841          0.001416   
34          -0.001062            0.000088          0.001150   
35          -0.001062            0.000044          0.001106   

    highest_return_300  lowest_return_450  trade_vol_450  liq_last_1  \
27            0.000841          -0.000576       24.39829   -3.802508   
34            0.000088          -0.001682       18.25532   -3.257787   
35            0.000044          -0.001682       15.21701   -4.008802   

    liq_last_2  liq_last_10  bidask_spread_0  bidask_spread_1  liq_last_1_150  \
27   -3.502729    -3.081749        13.821138        20.764227        0.000197   
34   -2.969625    -2.782810         2.333333         8.947369        0.000163   
35   -4.000357    -3.218102         5.496732         9.163399        0.000212   

    bidask_spread_0_150  bidask_spread_1_150  liq_last_1_300  ep_liq_1_300  \
27             8.263889            18.513890        0.003127      0.000271   
34            14.015625            23.140625        0.000315      0.000304   
35             5.800000            11.520000        0.000523      0.000180   

    bidask_spread_0_300  bidask_spread_1_300  liq_last_1_450  \
27             2.513514             9.837838        0.004479   
34             3.810126             8.759494        0.000521   
35             1.350000             4.837500        0.003814   

    bidask_spread_0_450  bidask_spread_1_450          tvpl1         tvpl5  \
27             1.754098             5.344262  218123.748150  75271.471144   
34             9.534654            14.603960   42530.742307  16887.138873   
35             2.324324             8.216216  243461.547308  71086.940167   

         tvpl_ep1  \
27   94451.390687   
34   87947.792197   
35  114380.542082   

    realized_volatility_mean0_nn2_realized_volatility_mean0_m_p1_mean  \
27                                           0.000188                   
34                                           0.000189                   
35                                           0.000182                   

    realized_volatility_mean0_nn2_bidask_spread_0_m_p1_mean  \
27                                           0.000188         
34                                           0.000122         
35                                           0.000155         

    realized_volatility_mean0_nn2_bidask_spread_1_m_p1_mean  \
27                                           0.000204         
34                                           0.000197         
35                                           0.000163         

    realized_volatility_mean0_nn2_highest_return_m_p1_mean  \
27                                           0.000135        
34                                           0.000168        
35                                           0.000190        

    realized_volatility_mean0_nn2_lowest_return_m_p1_mean  \
27                                           0.000208       
34                                           0.000208       
35                                           0.000160       

    realized_volatility_mean0_nn2_num_trades_m_p1_mean  \
27                                           0.000150    
34                                           0.000200    
35                                           0.000172    

    realized_volatility_mean0_nn2_high_low_gap_m_p1_mean  \
27                       

# Feature Selction A (This one is currently working for too long.)

## Exhaustive Feature Selection

This exhaustive feature selection algorithm is a wrapper approach for brute-force evaluation of feature subsets; the best subset is selected by optimizing a specified performance metric given an arbitrary regressor or classifier.

In [23]:
import pandas as pd

from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import roc_auc_score, r2_score
from sklearn.model_selection import train_test_split

from mlxtend.feature_selection import ExhaustiveFeatureSelector as EFS

In [ ]:
# 이 코드는 거의 안 돌아간다고 보면 된다. RTX3080으로 10000시간 돌았는데 안 끝남.

# exhaustive search

# in order to shorter search time for the demonstration
# i will ask the algorithm to try all possible 10 and 11
# feature combinations

# if you have access to a multicore or distributed computer
# system you can try more greedy searches

efs = EFS(RandomForestRegressor(n_estimators=5,
                                n_jobs=4,
                                random_state=0,
                                max_depth=2),
          min_features=1,
          max_features=2,
          scoring='r2',
          print_progress=True,
          cv=2)

efs = efs.fit(X, y)

In [ ]:
data.columns[list(efs.best_idx_)]

# Feature Selction B (이것도 이번 논문에서는 일단 제외)

## Embedded Methods: Linear Model Coefficients

train a Linear regression model and select features with higher coefficients.

In [24]:
# the features in the house dataset are in different scales
# so we train a scaler to scale them

scaler = StandardScaler()
scaler.fit(X)

# the LinearRegression object from sklearn is a non-regularised
# linear method. It fits by matrix multiplication and not 
# gradient descent.
# therefore we don't need to specify penalty and other parameters

sel_ = SelectFromModel(LinearRegression())

sel_.fit(scaler.transform(X), y)

# let's count the number of variables selected
selected_feat = X.columns[(sel_.get_support())]

# 저장할 파일 이름
file_name = "selected_feat_linear_coeff.pkl"

# selected_feat 변수를 pkl 파일로 저장
with open(file_name, 'wb') as file:
    pickle.dump(selected_feat, file)

print(f"{file_name} 파일이 저장되었습니다.")

print(len(selected_feat))


# and now, let's compare the  amount of selected features
# with the amount of features which coefficient is above the
# mean coefficient, to make sure we understand the output of
# sklearn

print('total features: {}'.format((X.shape[1])))

print('selected features: {}'.format(len(selected_feat)))

print(
    'features with coefficients greater than the mean coefficient: {}'.format(
        np.sum(
            np.abs(sel_.estimator_.coef_) > np.abs(
                sel_.estimator_.coef_).mean())))

selected_feat_linear_coeff.pkl 파일이 저장되었습니다.
1369
total features: 5595
selected features: 1369
features with coefficients greater than the mean coefficient: 1369


In [25]:
selected_feat

Index(['lowest_return_150', 'highest_return_150', 'high_low_gap_150',
       'realized_volatility_mean0_nn2_tvpl_c_mean',
       'realized_volatility_mean0_nn2_tvpl_epliq5_c_mean',
       'realized_volatility_mean0_nn2_BB_width_w10_c_mean',
       'realized_volatility_mean0_nn2_ep_liq_5_c_mean',
       'realized_volatility_mean0_nn2_liq_last_5_c_mean',
       'realized_volatility_mean0_nn2_liq_last_1_c_mean',
       'realized_volatility_mean0_nn2_highest_return_c_mean',
       ...
       'tvpl5_nn2_liq_last_5_m_p1_median', 'tvpl5_nn2_liq_last_1_m_p1_median',
       'tvpl5_nn2_trade_vol_m_p1_median',
       'tvpl5_nn2_lowest_return_m_p1_median',
       'tvpl5_nn2_realized_volatility_mean0_m_p2_median',
       'tvpl5_nn2_tvpl_epliq5_m_p2_median', 'tvpl5_nn2_ep_liq_5_m_p2_median',
       'tvpl5_nn2_liq_last_5_m_p2_median', 'tvpl5_nn2_trade_vol_m_p2_median',
       'tvpl5_nn4_tvpl_c_median'],
      dtype='object', length=1369)

# Feature Selction C

## Embedded Methods: Tree Importance

train a Linear regression model and select features with higher coefficients.

In [46]:
from sklearn.ensemble import RandomForestRegressor

In [47]:
# RandomForestRegressor 모델 학습
model = RandomForestRegressor(n_estimators=128, random_state=42, verbose=True)
model.fit(X, y)

# 특성 중요도 출력
feature_importances = model.feature_importances_
print("Feature Importances:", feature_importances)

# 특성 선택: 중요도가 높은 순서대로 특성 선택 (임계값 설정 가능)
selected_features_indices = feature_importances.argsort()[::-1]  # 중요도 내림차순 정렬
selected_features = X.columns[selected_features_indices]
print("Selected Features:", selected_features)

[Parallel(n_jobs=1)]: Using backend SequentialBackend with 1 concurrent workers.


Feature Importances: [1.21860331e-01 1.62425539e-03 2.75503974e-04 ... 9.73266961e-05
 1.16889099e-04 1.36803530e-04]
Selected Features: Index(['bidask_spread_1', 'realized_volatility_mean0', 'liq_last_10', 'tvpl5',
       'high_low_gap', 'trade_vol_450', 'bidask_spread_0', 'num_trades',
       'liq_last_2', 'tvpl_ep1',
       ...
       'realized_volatility_mean0_nn2_BB_width_w10_m_p1_mean',
       'BB_width_w20_nn2_bidask_spread_1_m_p1_mean',
       'tvpl_ep1_nn2_ep_liq_5_m_p1_mean', 'trade.tau_nn2_tvpl5_m_p1_median',
       'BB_width_w20_nn2_ep_liq_5_m_p1_median',
       'ep_liq_1_nn2_trade_vol_m_p1_mean',
       'bidask_spread_1_nn2_all_nn_m_p1_median',
       'tvpl_ep5_nn2_lowest_return_m_p1_mean',
       'tvpl_ep5_nn2_bidask_spread_0_m_p1_mean',
       'tvpl_ep1_nn2_tvpl_ep5_m_p1_mean'],
      dtype='object', length=4995)


[Parallel(n_jobs=1)]: Done 128 out of 128 | elapsed: 334.2min finished


In [49]:
# 저장할 파일 이름
file_name = "selected_feat_RF_{}_{}_{}.pkl".format(coin, target_var_3, corr_cutpoint)

# selected_feat 변수를 pkl 파일로 저장
with open(file_name, 'wb') as file:
    pickle.dump(selected_features, file)

print(f"{file_name} 파일이 저장되었습니다.")

print(len(selected_features))


# 저장할 파일 이름
file_name2 = "feature_importances_RF_{}_{}_{}.pkl".format(coin, target_var_3, corr_cutpoint)

# selected_feat 변수를 pkl 파일로 저장
with open(file_name2, 'wb') as file:
    pickle.dump(feature_importances, file)

print(f"{file_name2} 파일이 저장되었습니다.")

print(len(feature_importances))


selected_feat_RF_BTC_dv5_90.pkl 파일이 저장되었습니다.
4995
feature_importances_RF_BTC_dv5_90.pkl 파일이 저장되었습니다.
4995


In [51]:
# 저장된 Pickle 파일을 로드하는 방법

file_name = "selected_feat_RF_{}_{}_{}.pkl".format(coin, target_var_3, corr_cutpoint)

with open(file_name, 'rb') as f:
    selected_features = pickle.load(f)

print(len(selected_features))


# 저장된 Pickle 파일을 로드하는 방법
file_name2 = "feature_importances_RF_{}_{}_{}.pkl".format(coin, target_var_3, corr_cutpoint)

with open(file_name2, 'rb') as f2:
    feature_importances_ranfo = pickle.load(f2)

print(len(feature_importances_ranfo))


4995
4995


In [52]:
# 리스트를 DataFrame으로 변환
data = {'Name': list(selected_features), 'Importance': sorted(list(feature_importances), reverse=True)}
df = pd.DataFrame(data)

# DataFrame 출력
df.head(50)


Name  Importance
0                                     bidask_spread_1    0.205427
1                           realized_volatility_mean0    0.121860
2                                         liq_last_10    0.019989
3                                               tvpl5    0.007778
4                                        high_low_gap    0.006244
5                                       trade_vol_450    0.002227
6                                     bidask_spread_0    0.001734
7                                          num_trades    0.001624
8                                          liq_last_2    0.001295
9                                            tvpl_ep1    0.001286
10                                       BB_width_w40    0.000926
11                                       BB_width_w20    0.000911
12                   ep_liq_1_nn64_ep_liq_5_m_p1_mean    0.000816
13                liq_last_5_nn32_high5_abs_nn_m_mean    0.000809
14             BB_width_w20_nn48_tvpl_ep1_m_p1_median    0.000595
15              lowest_return_nn64_ep_liq_5_m_p1_mean    0.000585
16             BB_width_w20_nn48_ep_liq_5_m_p1_median    0.000566
17                                       ep_liq_1_300    0.000557
18                   ep_liq_5_nn48_low5_abs_nn_m_mean    0.000517
19                                   high_low_gap_150    0.000517
20                                         liq_last_1    0.000470
21               BB_width_w20_nn48_ep_liq_5_m_p1_mean    0.000468
22                   ep_liq_5_nn48_tvpl_ep1_m_p1_mean    0.000449
23  realized_volatility_mean0_nn64_ep_liq_1_m_p1_m...    0.000435
24  realized_volatility_mean0_nn48_ep_liq_1_m_p1_mean    0.000405
25                                              tvpl1    0.000394
26                   tvpl_ep1_nn48_all_nn_m_p1_median    0.000384
27            liq_last_5_nn48_lowest_return_m_p1_mean    0.000381
28                                bidask_spread_1_450    0.000370
29    tvpl5_nn4_realized_volatility_mean0_m_p1_median    0.000353
30                     tvpl_ep1_nn32_low5_nn_m_median    0.000349
31               lowest_return_nn32_tvpl1_m_p1_median    0.000345
32                   tvpl_ep1_nn48_tvpl_ep5_m_p1_mean    0.000343
33  dv5_realized_volatility_mean0_nn48_high5_abs_n...    0.000337
34              lowest_return_nn32_all_nn_m_p1_median    0.000335
35                      trade.tau_nn64_low5_nn_m_mean    0.000333
36                ep_liq_1_nn64_trade.tau_m_p1_median    0.000330
37                   BB_width_w20_nn16_low5_nn_m_mean    0.000328
38                     ep_liq_1_nn64_all_nn_m_p1_mean    0.000316
39             BB_width_w20_nn32_low5_abs_nn_m_median    0.000314
40                 tvpl_ep1_nn64_tvpl_ep1_m_p1_median    0.000312
41                      realized_volatility_mean0_150    0.000311
42                 BB_width_w20_nn32_low5_nn_m_median    0.000308
43                     ep_liq_1_nn32_all_nn_m_p1_mean    0.000307
44     highest_return_nn64_highest_return_m_p1_median    0.000304
45           BB_width_w20_nn48_high_low_gap_m_p1_mean    0.000301
46             tvpl_ep1_nn64_high_low_gap_m_p1_median    0.000297
47                tvpl_ep1_nn64_trade.tau_m_p1_median    0.000297
48                       ep_liq_5_nn48_low5_nn_m_mean    0.000295
49                        tvpl1_nn64_low5_nn_m_median    0.000294

In [ ]:
df.to_csv('D:/OneDrive - 한동대학교/PROJECT/트머프로젝트/output/temp_RF_important_features.csv')